In [1]:
import altair as alt
import pandas as pd
import geopandas as gpd
from vega_datasets import data
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
airports_url = "airports-extended.csv"
airports = pd.read_csv(airports_url)
airports

Airport ID                                         Name          City  \
0               1                               Goroka Airport        Goroka   
1               2                               Madang Airport        Madang   
2               3                 Mount Hagen Kagamuga Airport   Mount Hagen   
3               4                               Nadzab Airport        Nadzab   
4               5  Port Moresby Jacksons International Airport  Port Moresby   
...           ...                                          ...           ...   
12663       14107                        Ulan-Ude East Airport      Ulan Ude   
12664       14108                         Krechevitsy Air Base      Novgorod   
12665       14109                  Desierto de Atacama Airport       Copiapo   
12666       14110                           Melitopol Air Base     Melitopol   
12667       14111                    Lincoln Train Station LNK       Lincoln   

                Country IATA  ICAO  Longitude    Latitude  Altitude  TimeZone  \
0      Papua New Guinea  GKA  AYGA  -6.081690  145.391998      5282      10.0   
1      Papua New Guinea  MAG  AYMD  -5.207080  145.789002        20      10.0   
2      Papua New Guinea  HGU  AYMH  -5.826790  144.296005      5388      10.0   
3      Papua New Guinea  LAE  AYNZ  -6.569803  146.725977       239      10.0   
4      Papua New Guinea  POM  AYPY  -9.443380  147.220001       146      10.0   
...                 ...  ...   ...        ...         ...       ...       ...   
12663            Russia   \N  XIUW  51.849998  107.737999      1670       NaN   
12664            Russia   \N  ULLK  58.625000   31.385000        85       NaN   
12665             Chile  CPO  SCAT -27.261200  -70.779198       670       NaN   
12666           Ukraine   \N  UKDM  46.880001   35.305000         0       NaN   
12667     United States   \N    \N  40.815833  -96.713889      1176      -5.0   

      DST Tz Database Time Zone     Type       Source  
0       U  Pacific/Port_Moresby  airport  OurAirports  
1       U  Pacific/Port_Moresby  airport  OurAirports  
2       U  Pacific/Port_Moresby  airport  OurAirports  
3       U  Pacific/Port_Moresby  airport  OurAirports  
4       U  Pacific/Port_Moresby  airport  OurAirports  
...    ..                   ...      ...          ...  
12663  \N                    \N  airport  OurAirports  
12664  \N                    \N  airport  OurAirports  
12665  \N                    \N  airport  OurAirports  
12666  \N                    \N  airport  OurAirports  
12667   A                    \N       \N           \N  

[12668 rows x 14 columns]

Derive US airports

In [3]:
us_airports = airports.where(airports["Country"] =="United States")
us_airports.dropna(inplace=True)
us_airports["Airport ID"] = us_airports["Airport ID"].astype(str)
us_airports["Airport ID"] = us_airports["Airport ID"].str.replace(".0","",regex=True)

us_airports["Type"].unique()  #column has unknown values that will be dropped
# only show known values
us_airports = us_airports.loc[(us_airports["Type"] == "airport") | (us_airports["Type"] == "station") | (us_airports["Type"] == "port")]
us_airports


Airport ID                        Name             City        Country  \
3223        3411  Barter Island LRRS Airport    Barter Island  United States   
3224        3412      Wainwright Air Station  Fort Wainwright  United States   
3225        3413  Cape Lisburne LRRS Airport    Cape Lisburne  United States   
3226        3414      Point Lay LRRS Airport        Point Lay  United States   
3227        3415  Hilo International Airport             Hilo  United States   
...          ...                         ...              ...            ...   
12264        137            Seldovia Airport         Seldovia  United States   
12314      13757    Vidalia Regional Airport          Vidalia  United States   
12315      13758   Granbury Regional Airport         Granbury  United States   
12316      13759       Oswego County Airport           Fulton  United States   
12360        133  Mitchell Municipal Airport         Mitchell  United States   

      IATA  ICAO  Longitude    Latitude  Altitude  TimeZone DST  \
3223   BTI  PABA  70.134003 -143.582001       2.0      -9.0   A   
3224    \N  PAWT  70.613403 -159.860001      35.0      -9.0   A   
3225   LUR  PALU  68.875099 -166.110001      16.0      -9.0   A   
3226   PIZ  PPIZ  69.732903 -163.005005      22.0      -9.0   A   
3227   ITO  PHTO  19.721399 -155.048004      38.0     -10.0   N   
...    ...   ...        ...         ...       ...       ...  ..   
12264  SOV  PASO  59.442402 -151.703995      29.0      -9.0   A   
12314  VDI  KVDI  32.192699  -82.371201     275.0      -4.0   A   
12315   \N  KGDJ  32.444401  -97.816902     778.0      -5.0   A   
12316   \N  KFZY  43.350800  -76.388100     475.0      -4.0   A   
12360  MHE  KMHE  43.774799  -98.038597    1304.0      -6.0   A   

      Tz Database Time Zone     Type       Source  
3223      America/Anchorage  airport  OurAirports  
3224      America/Anchorage  airport  OurAirports  
3225      America/Anchorage  airport  OurAirports  
3226      America/Anchorage  airport  OurAirports  
3227       Pacific/Honolulu  airport  OurAirports  
...                     ...      ...          ...  
12264                    \N  airport  OurAirports  
12314                    \N  airport  OurAirports  
12315                    \N  airport  OurAirports  
12316                    \N  airport  OurAirports  
12360                    \N  airport  OurAirports  

[2077 rows x 14 columns]

Import Us states data

In [4]:
us_cities = pd.read_csv("uscities.csv")   # https://www.kaggle.com/datasets/sergejnuss/united-states-cities-database
us_states = pd.read_csv("us_states.csv")

us_cities  = us_cities.filter(["city","state_id"])

airports_cities = pd.merge(us_airports,us_cities,how="inner", left_on="City",right_on="city")
airports_states = pd.merge(airports_cities,us_states,how="inner", left_on="state_id",right_on="STUSAB")
path = "airports_states.csv"
airports_states.to_csv(path)
airports_states["Type Counts"] = airports_states.groupby(["Type","STATE_NAME"])["Type"].transform("count")

airports_states

Airport ID                               Name        City        Country  \
0          3414             Point Lay LRRS Airport   Point Lay  United States   
1          3417                    Bettles Airport     Bettles  United States   
2            34                 Fort Yukon Airport  Fort Yukon  United States   
3          3429                    Iliamna Airport     Iliamna  United States   
4          3438                      Merrill Field   Anchorage  United States   
...         ...                                ...         ...            ...   
7243         95              South Norwalk Station     Norwalk  United States   
7244        646           New London Union Station  New London  United States   
7245        135  Meriden Markham Municipal Airport     Meriden  United States   
7246        115           Rockville Amtrak Station   Rockville  United States   
7247      12796                  Danielson Airport   Danielson  United States   

     IATA  ICAO  Longitude    Latitude  Altitude  TimeZone  ...  \
0     PIZ  PPIZ  69.732903 -163.005005      22.0      -9.0  ...   
1     BTT  PABT  66.913902 -151.529007     647.0      -9.0  ...   
2     FYU  PFYU  66.571503 -145.250000     433.0      -9.0  ...   
3     ILI  PAIL  59.754398 -154.910996     192.0      -9.0  ...   
4     MRI  PAMR  61.213501 -149.843994     137.0      -9.0  ...   
...   ...   ...        ...         ...       ...       ...  ...   
7243   \N    \N  41.096730  -73.421132      36.0      -5.0  ...   
7244   \N    \N  41.354167  -72.093056       0.0      -5.0  ...   
7245   \N  KMMK  41.508701  -72.829498     103.0      -5.0  ...   
7246   \N    \N  39.084497  -77.148261       0.0      -5.0  ...   
7247   \N  KLZD  41.819698  -71.901001     238.0      -5.0  ...   

     Tz Database Time Zone     Type       Source        city state_id STATE  \
0        America/Anchorage  airport  OurAirports   Point Lay       AK     2   
1        America/Anchorage  airport  OurAirports     Bettles       AK     2   
2        America/Anchorage  airport  OurAirports  Fort Yukon       AK     2   
3        America/Anchorage  airport  OurAirports     Iliamna       AK     2   
4        America/Anchorage  airport  OurAirports   Anchorage       AK     2   
...                    ...      ...          ...         ...      ...   ...   
7243      America/New_York  station         User     Norwalk       CT     9   
7244                    \N  station         User  New London       CT     9   
7245                    \N  airport  OurAirports     Meriden       CT     9   
7246                    \N  station         User   Rockville       CT     9   
7247                    \N  airport  OurAirports   Danielson       CT     9   

      STUSAB   STATE_NAME  STATENS  Type Counts  
0         AK       Alaska  1785533          216  
1         AK       Alaska  1785533          216  
2         AK       Alaska  1785533          216  
3         AK       Alaska  1785533          216  
4         AK       Alaska  1785533          216  
...      ...          ...      ...          ...  
7243      CT  Connecticut  1779780           10  
7244      CT  Connecticut  1779780           10  
7245      CT  Connecticut  1779780           15  
7246      CT  Connecticut  1779780           10  
7247      CT  Connecticut  1779780           15  

[7248 rows x 21 columns]

In [9]:
states = gpd.read_file("us_states.json")

plot = alt.concat( *  (
    alt.Chart(states,title=type).mark_geoshape().encode(
        color="Type Counts:Q",
        tooltip=['STATE_NAME:N',"Type Counts:Q"],
    ).transform_lookup(
        "name",
        alt.LookupData(
            airports_states[airports_states['Type']==type],
            "STATE_NAME",
            fields=airports_states.columns.to_list())
        ).project(type='albersUsa')
    
    for type in list(airports_states.Type.unique())
    ), columns=3, title="The number of different kinds of 'ports' in US States"
).configure_title(align="center",anchor="middle",fontSize=15, offset=20)

plot

alt.ConcatChart(...)